In [1]:
import sys
sys.path.append('..')
import SRNF_match
import H2_match as gm
import utils.input_output as input_output
import numpy as np
import torch
use_cuda = 1
torchdeviceId = torch.device('cuda:0') if use_cuda else 'cpu'
torchdtype = torch.float32
import plotly.graph_objects as go

In [2]:
N=2 
[VS,FS,FunS] = input_output.loadData("TestData/faces/face-reference.ply")  
VS=VS/10
[VS,FS]= input_output.decimate_mesh(VS,FS,int(FS.shape[0]/16))   
FunS=np.zeros((int(np.size(VS)/3),)) 
sources = [[VS,FS]]

[VT,FT,FunT] = input_output.loadData("TestData/faces/face-rage.ply") 
VT=VT/10
[VT,FT]= input_output.decimate_mesh(VT,FT,int(FT.shape[0]/16))
FunT=np.zeros((int(np.size(VT)/3),)) 
targets= [[VT,FT]]

source=sources[0] 
target=targets[0]

In [3]:
a0=.01
a1=100
b1=100
c1=.2
d1=.01
a2=.01


param1 = { 'weight_coef_dist_T': 10**1,'weight_coef_dist_S': 10**1,'sig_geom':.4,\
          'max_iter': 2000,'time_steps': 2, 'tri_unsample': True, 'index':0}

param2 = {'weight_coef_dist_T': 10**2,'weight_coef_dist_S': 10**2,'sig_geom':.3,\
          'max_iter': 1000,'time_steps': 2, 'tri_unsample': False, 'index':1}

param3 = {'weight_coef_dist_T': 10**3,'weight_coef_dist_S': 10**3,'sig_geom':.2,\
          'max_iter': 1000, 'time_steps': 2, 'tri_unsample': False, 'index':1}

param4 = {'weight_coef_dist_T': 10**4,'weight_coef_dist_S': 10**4,'sig_geom':.1,\
          'max_iter': 1000, 'time_steps': 3, 'tri_unsample': True, 'index':1}

param5 = {'weight_coef_dist_T': 10**5,'weight_coef_dist_S': 10**5,'sig_geom':.1,\
          'max_iter': 1000, 'time_steps': 4, 'tri_unsample': False, 'index':2}

param6 = { 'weight_coef_dist_T': 10**6,'weight_coef_dist_S': 10**6,'sig_geom':.05,\
          'max_iter': 1000, 'time_steps': 5, 'tri_unsample': False, 'index':2}



paramlist=[param1,param2,param3,param4,param5,param6]

In [4]:
geod,F0=gm.H2MultiRes(source,target,a0,a1,b1,c1,d1,a2,2,paramlist)

(3614, 3)
(903, 3)
(225, 3)
0 (225, 3)
1 (900, 3)
2 (900, 3)
3 (900, 3)
4 (3600, 3)
5 (3600, 3)
6 (3600, 3)


In [5]:
ls=input_output.makeGeodMeshes(geod,F0,o_source=source,o_target=target, stepsize=2, axis=[0,0,1],angle=-1*np.pi)
mesh = ls[0]    
for i in range(1,len(ls)):
    mesh += ls[i]
[V,F,color]=input_output.getDataFromMesh(mesh)

In [6]:
fig = go.Figure(
    data=[
        go.Mesh3d(
            x=V[:,0],
            y=V[:,1],
            z=V[:,2],
            i=F[:,0],
            j=F[:,1],
            k=F[:,2],
            opacity=1.0)
    ],
    layout=dict(
        scene=dict(
            xaxis=dict(visible=False),
            yaxis=dict(visible=False),
            zaxis=dict(visible=False),
            aspectmode='data'
        )
    )
)
fig.show()